In [1]:
import numpy as np
import pandas as pd

from sklearn.model_selection import GridSearchCV, StratifiedKFold
from sklearn.pipeline import Pipeline
from sklearn.preprocessing import StandardScaler
from sklearn.decomposition import PCA
from sklearn.feature_selection import SelectKBest, f_classif
from sklearn.linear_model import LogisticRegression
from sklearn.svm import SVC
from sklearn.neighbors import KNeighborsClassifier
from sklearn.neural_network import MLPClassifier
from sklearn.ensemble import AdaBoostClassifier
from sklearn.metrics import accuracy_score
from sklearn.utils import resample

# Chargement des données
X_train = np.load("data/X_train.npy")
X_test = np.load("data/X_test.npy")
y_train = np.load("data/y_train.npy")
y_test = np.load("data/y_test.npy")

# Équilibrage si nécessaire
unique, counts = np.unique(y_train, return_counts=True)
if np.min(counts) / np.max(counts) < 0.8:
    class_0 = X_train[y_train == 0]
    class_1 = X_train[y_train == 1]
    y0 = y_train[y_train == 0]
    y1 = y_train[y_train == 1]
    if len(y0) < len(y1):
        class_0, y0 = resample(class_0, y0, replace=True, n_samples=len(y1), random_state=42)
    else:
        class_1, y1 = resample(class_1, y1, replace=True, n_samples=len(y0), random_state=42)
    X_train = np.vstack((class_0, class_1))
    y_train = np.concatenate((y0, y1))

# Grilles enrichies
classifiers = {
    "LogisticRegression": (
        LogisticRegression(solver="saga", max_iter=10000),
        {
            "logisticregression__C": [0.01, 0.1, 1, 10, 100],
            "logisticregression__penalty": ["l1", "l2"]
        }
    ),
    "SVC": (
        SVC(),
        {
            "svc__C": [0.5, 1, 2, 3, 5, 10],
            "svc__gamma": [0.01, 0.05, 0.1, 0.2, "scale"],
            "svc__kernel": ["rbf"]
        }
    ),
    "KNN": (
        KNeighborsClassifier(),
        {
            "knn__n_neighbors": [3, 5, 7, 9, 11],
            "knn__weights": ["uniform", "distance"]
        }
    ),
    "MLP": (
        MLPClassifier(max_iter=2000),
        {
            "mlp__hidden_layer_sizes": [(100,), (128, 64), (256, 128)],
            "mlp__alpha": [0.0001, 0.001],
            "mlp__solver": ["adam"],
            "mlp__early_stopping": [True],
            "mlp__learning_rate": ["adaptive"]
        }
    ),
    "AdaBoost": (
        AdaBoostClassifier(),
        {
            "adaboost__n_estimators": [50, 100, 200, 300],
            "adaboost__learning_rate": [0.01, 0.1, 0.5, 1]
        }
    )
}


# Sélections de features
feature_selectors = {
    "none": None,
    "pca": PCA(n_components=0.95),
    "selectkbest": SelectKBest(score_func=f_classif, k=10)
}

# Benchmark
cv = StratifiedKFold(n_splits=10, shuffle=True, random_state=42)
results = []

for fs_name, fs in feature_selectors.items():
    for clf_name, (clf, grid) in classifiers.items():
        steps = [("scaler", StandardScaler())]
        if fs_name != "none":
            steps.append(("feature_selection", fs))
        steps.append((clf_name.lower(), clf))
        pipeline = Pipeline(steps)

        grid_search = GridSearchCV(
            pipeline, grid, cv=cv, scoring="accuracy", n_jobs=-1, verbose=0
        )
        grid_search.fit(X_train, y_train)

        y_pred = grid_search.predict(X_test)
        test_acc = accuracy_score(y_test, y_pred)

        results.append({
            "Model": clf_name,
            "Feature Selection": fs_name,
            "Best Params": grid_search.best_params_,
            "CV Accuracy": grid_search.best_score_,
            "Test Accuracy": test_acc
        })

df_results = pd.DataFrame(results).sort_values(by="Test Accuracy", ascending=False)
df_results.reset_index(drop=True, inplace=True)
df_results


/Users/rayandrissi/dev/epita/majeur/FTML/FTML-Epita-/venv/lib/python3.11/site-packages/sklearn/utils/extmath.py:203: RuntimeWarning: divide by zero encountered in matmul
  ret = a @ b
/Users/rayandrissi/dev/epita/majeur/FTML/FTML-Epita-/venv/lib/python3.11/site-packages/sklearn/utils/extmath.py:203: RuntimeWarning: overflow encountered in matmul
  ret = a @ b
/Users/rayandrissi/dev/epita/majeur/FTML/FTML-Epita-/venv/lib/python3.11/site-packages/sklearn/utils/extmath.py:203: RuntimeWarning: invalid value encountered in matmul
  ret = a @ b
/Users/rayandrissi/dev/epita/majeur/FTML/FTML-Epita-/venv/lib/python3.11/site-packages/sklearn/utils/extmath.py:203: RuntimeWarning: divide by zero encountered in matmul
  ret = a @ b
/Users/rayandrissi/dev/epita/majeur/FTML/FTML-Epita-/venv/lib/python3.11/site-packages/sklearn/utils/extmath.py:203: RuntimeWarning: overflow encountered in matmul
  ret = a @ b
/Users/rayandrissi/dev/epita/majeur/FTML/FTML-Epita-/venv/lib/python3.11/site-packages/sklear

Model Feature Selection  \
0                  SVC              none   
1                  SVC       selectkbest   
2                  MLP       selectkbest   
3                  MLP              none   
4                  KNN              none   
5                  SVC               pca   
6                  MLP               pca   
7                  KNN       selectkbest   
8             AdaBoost              none   
9                  KNN               pca   
10  LogisticRegression              none   
11  LogisticRegression               pca   
12  LogisticRegression       selectkbest   
13            AdaBoost       selectkbest   
14            AdaBoost               pca   

                                          Best Params  CV Accuracy  \
0   {'svc__C': 5, 'svc__gamma': 0.05, 'svc__kernel...       0.7770   
1   {'svc__C': 2, 'svc__gamma': 0.1, 'svc__kernel'...       0.7875   
2   {'mlp__alpha': 0.0001, 'mlp__early_stopping': ...       0.7775   
3   {'mlp__alpha': 0.001, 'mlp__early_stopping': T...       0.7450   
4   {'knn__n_neighbors': 11, 'knn__weights': 'unif...       0.7390   
5   {'svc__C': 5, 'svc__gamma': 0.1, 'svc__kernel'...       0.7535   
6   {'mlp__alpha': 0.001, 'mlp__early_stopping': T...       0.7270   
7   {'knn__n_neighbors': 11, 'knn__weights': 'unif...       0.7590   
8   {'adaboost__learning_rate': 0.5, 'adaboost__n_...       0.7155   
9   {'knn__n_neighbors': 11, 'knn__weights': 'unif...       0.7155   
10  {'logisticregression__C': 0.1, 'logisticregres...       0.7130   
11  {'logisticregression__C': 1, 'logisticregressi...       0.7075   
12  {'logisticregression__C': 1, 'logisticregressi...       0.7160   
13  {'adaboost__learning_rate': 0.1, 'adaboost__n_...       0.7110   
14  {'adaboost__learning_rate': 0.5, 'adaboost__n_...       0.7020   

    Test Accuracy  
0          0.8005  
1          0.7855  
2          0.7830  
3          0.7775  
4          0.7750  
5          0.7750  
6          0.7680  
7          0.7605  
8          0.7495  
9          0.7490  
10         0.7485  
11         0.7435  
12         0.7395  
13         0.7395  
14         0.7195